In [87]:
!pip install speechpy
!pip install soundfile
!pip install tables

     |████████████████████████████████| 4.3MB 207kB/s eta 0:00:01


In [12]:
import numpy as np
import pandas as pd
import soundfile as sf
import scipy.io.wavfile as wav
import speechpy
import json
import os
import math
import keras as k
import dask.dataframe as dd
from multiprocessing import Queue, Process, Pool

%config IPCompleter.greedy=True

For audio processing I will use `speechpy` as it is the fastest of the well known libraries:

![speed_comp](https://camo.githubusercontent.com/1465ddaba9f99df4ff86ef800ef4598f35c12698/68747470733a2f2f696d61676573322e696d67626f782e636f6d2f64652f31302f6f4e5a776b49694b5f6f2e706e67)
> Source: [sonopy](https://github.com/MycroftAI/sonopy)

In [121]:
index = np.arange(0, 10, 0.1)
index2 = np.arange(3, 13, 0.2)

df = pd.DataFrame(data={'A': index}, index=index)
df2 = pd.DataFrame(data={'B': index}, index=index)
df2.index = df2.index + 1
df.join(df2)

A    B
0.0  0.0  NaN
0.1  0.1  NaN
0.2  0.2  NaN
0.3  0.3  NaN
0.4  0.4  NaN
0.5  0.5  NaN
0.6  0.6  NaN
0.7  0.7  NaN
0.8  0.8  NaN
0.9  0.9  NaN
1.0  1.0  0.0
1.1  1.1  0.1
1.2  1.2  NaN
1.3  1.3  0.3
1.4  1.4  NaN
1.5  1.5  0.5
1.6  1.6  0.6
1.7  1.7  0.7
1.8  1.8  0.8
1.9  1.9  NaN
2.0  2.0  1.0
2.1  2.1  1.1
2.2  2.2  1.2
2.3  2.3  NaN
2.4  2.4  1.4
2.5  2.5  1.5
2.6  2.6  1.6
2.7  2.7  1.7
2.8  2.8  NaN
2.9  2.9  1.9
..   ...  ...
7.0  7.0  6.0
7.1  7.1  6.1
7.2  7.2  6.2
7.3  7.3  6.3
7.4  7.4  6.4
7.5  7.5  6.5
7.6  7.6  6.6
7.7  7.7  6.7
7.8  7.8  6.8
7.9  7.9  6.9
8.0  8.0  7.0
8.1  8.1  NaN
8.2  8.2  NaN
8.3  8.3  7.3
8.4  8.4  7.4
8.5  8.5  7.5
8.6  8.6  NaN
8.7  8.7  NaN
8.8  8.8  7.8
8.9  8.9  7.9
9.0  9.0  8.0
9.1  9.1  8.1
9.2  9.2  8.2
9.3  9.3  8.3
9.4  9.4  8.4
9.5  9.5  8.5
9.6  9.6  NaN
9.7  9.7  8.7
9.8  9.8  8.8
9.9  9.9  8.9

[100 rows x 2 columns]

In [173]:
def file2mfcc(file_name, frame_length=0.20, frame_stride=0.1, recreate=False):
    """ recreate: whether to recreate existing .npy MFCC"""
    
    dir_name = file_name[:file_name.index('blocks')]
    file_wav, file_ogg = None, None
    
#     check for existing .wav or .npy cache
    for file in os.listdir(dir_name):
#         if file.endswith('.wav'):
#             file_wav = os.path.join(dir_name, file)
#         if file.endswith('.npy') and not recreate:
#             return np.load(os.path.join(dir_name, file))
        if file.endswith('.mfcc') and not recreate:
            return pd.read_hdf((os.path.join(dir_name, file)))
            
#     if none .wav found, create it
    for file in os.listdir(dir_name):
        if file.endswith('.ogg'):
            file_ogg = os.path.join(dir_name, file)
            if not file_wav:
                data, samplerate = sf.read(file_ogg)
                file_wav = f'{file_ogg[:-4]}.wav'
                sf.write(file_wav, data, samplerate)

    fs, signal = wav.read(file_wav)
    print(fs, signal.shape)
    
#     Stereo to mono
    if signal.shape[1] == 2:
        signal = (signal[:, 0] + signal[:, 1]) / 2
    else:
        signal = signal[:, 0]

    # Pre-emphasize
    signal_preemphasized = speechpy.processing.preemphasis(signal, cof=0.98)

    # Extract MFCC features
    mfcc = speechpy.feature.mfcc(signal, sampling_frequency=fs, frame_length=frame_length, 
                                 frame_stride=frame_stride, num_filters=40, fft_length=512,
                                 low_frequency=0, high_frequency=None, num_cepstral=13)
    
#     Normalize
    mfcc_cmvn = speechpy.processing.cmvnw(mfcc,win_size=301,variance_normalization=True)
    
#     Cache results and clean .wav to save space
#     np.save(f'{file_wav[:-4]}.mfcc.npy', mfcc_cmvn)
    if file_ogg:
        os.remove(file_wav)
        
    index = np.arange(0, (len(mfcc) - 0.5) * frame_stride, frame_stride) + frame_length
    print(index.shape)
    print(index)
    df = pd.DataFrame(data=mfcc_cmvn, index=index).apply(np.array, axis=1)
    df.to_hdf(f'{file_wav[:-4]}.mfcc', 'mfcc', mode='w', format='fixed')
    return df

def process_cell(cell, side):
    res = cell[:, :, side, :]
    
    mx = res.max()
    mx_index = np.unravel_index(res.argmax(), res.shape)
    pred = [None for _ in range(3)]
    
    for dim in range(3):
        pred[dim] = np.zeros(res.shape[dim] + 1)
        
        if mx < 0.5:
            pred[dim][-1] = 1
        else:
            pred[dim][mx_index[dim]] = 1
    
#     print(pred)
    return pred

def change_output(df: pd.DataFrame):
    left, right = df.apply(lambda cell: process_cell(cell, 0)), df.apply(lambda cell: process_cell(cell, 1))
    
    left = pd.DataFrame(left.to_list(), columns=[f'l_dim{x}' for x in range(3)], index=left.index)
    right = pd.DataFrame(right.to_list(), columns=[f'r_dim{x}' for x in range(3)], index=right.index)
    
    return left.join(right)
    
def process_file(file_path, recreate=False):
    print(f'Processing {file_path}')
    try:
        df = pd.read_pickle(file_path)
    except Exception as e:
        print(f'Caught Error: {e}')
        return 
    
    # all in one serialization (99.5 % with bad metric)
    #     df['output'] = df_col2series(df, ['output'])
    df = df.join(change_output(df['output']))
    df['shifted'] = df['output'].shift(1, fill_value=[np.zeros(df['output'].iloc[0].shape)])
    df['times'] = df_col2series(df, ['prev', 'next'])
    df['name'] = f'{file_path}'
    
    mfcc = file2mfcc(file_path, recreate=recreate)
    mfcc.name = 'mfcc'
    round_index = mfcc.index.values[1] - mfcc.index.values[0]
    df.index = np.floor(df['time'] / round_index).astype(int)
    mfcc.index = (mfcc.index / round_index).astype(int)
    
    df = df.join(mfcc)
    df.index = df['time']

    return df
    
file = '../data/Army Of The Night/blocks/Expert.pkl'
file2mfcc(file, recreate=False)
process_file(file).iloc[0]

Processing ../data/Army Of The Night/blocks/Expert.pkl


output     [[[[0. 1. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...
time                                                 3.08211
prev                                                 3.08211
next                                               0.0821053
l_dim0                                  [1.0, 0.0, 0.0, 0.0]
l_dim1                             [1.0, 0.0, 0.0, 0.0, 0.0]
l_dim2     [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
r_dim0                                  [0.0, 0.0, 0.0, 1.0]
r_dim1                             [0.0, 0.0, 0.0, 0.0, 1.0]
r_dim2     [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
shifted    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...
times              [3.0821052631578945, 0.08210526315789446]
name             ../data/Army Of The Night/blocks/Expert.pkl
mfcc       [0.36976948, -1.4347119, 0.909154, 0.62588304,...
Name: 3.0821052631578945, dtype: object

In [174]:
process_file('../data/1My Truth/blocks/Hard.pkl')

Processing ../data/1My Truth/blocks/Hard.pkl


output        time  \
time                                                                        
2.527397    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    2.527397   
3.349315    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    3.349315   
4.171233    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    4.171233   
4.376712    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    4.376712   
4.582192    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    4.582192   
4.787671    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    4.787671   
4.993151    [[[[0. 1. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    4.993151   
5.815068    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    5.815068   
6.636986    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    6.636986   
6.842466    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    6.842466   
7.047945    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    7.047945   
7.253425    [[[[1. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    7.253425   
7.458904    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    7.458904   
8.691781    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    8.691781   
9.102740    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    9.102740   
9.719178    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    9.719178   
9.924658    [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...    9.924658   
11.630137   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   11.630137   
12.053425   [[[[1. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   12.053425   
12.439726   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   12.439726   
13.224658   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   13.224658   
14.034247   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   14.034247   
14.239726   [[[[0. 1. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   14.239726   
14.445205   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   14.445205   
14.650685   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   14.650685   
14.856164   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   14.856164   
15.727397   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   15.727397   
16.512329   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   16.512329   
16.717808   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   16.717808   
16.947945   [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...   16.947945   
...                                                       ...         ...   
286.910959  [[[[1. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  286.910959   
287.732877  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  287.732877   
287.938356  [[[[0. 1. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  287.938356   
288.143836  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  288.143836   
288.349315  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  288.349315   
288.554795  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  288.554795   
288.760274  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  288.760274   
288.965753  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  288.965753   
289.171233  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  289.171233   
289.376712  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  289.376712   
289.582192  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  289.582192   
289.787671  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  289.787671   
289.993151  [[[[1. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  289.993151   
290.198630  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  290.198630   
290.404110  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  290.404110   
291.020548  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  291.020548   
291.842466  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  291.842466   
292.664384  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  292.664384   
292.869863  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0. 0. 0. ...  292.869863   
293.075342  [[[[0. 0. 0. 0. 0. 0. 0. 0. 0.], [0. 0.

In [175]:
def df_col2numpy(df, col_names):
    ser = df.apply(lambda row: np.array([row[col] for col in col_names]).flatten(), axis=1)
    arr = np.array(ser.values.tolist())
    return arr

def df_col2series(df, col_names):
    if len(col_names) == 1:
        ser = df[col_names[0]].map(lambda cell: np.array([cell]).flatten())
    ser = df.apply(lambda row: np.array([row[col] for col in col_names]).flatten(), axis=1)
    return ser

def get_file_paths(path, hard_max):
    file_paths = []
    counter = 0
    
    for root, dirs, files in os.walk(path, topdown=False):
        if counter > hard_max:
                break
        for name in files:
            if root[-6:] == 'blocks':
                print(f'#{counter:5} {root}/{name}')
                file_paths.append(os.path.join(root, name))
                
                counter += 1
                
    return file_paths
    
    
X_list = []
Y = []
HARD_MAX = 20
path = '../data'
columns = ['times', 'name', 'time', 'mfcc'] + [f'{side}_dim{i}' for i in range(3) for side in 'rl']

pool = Pool(processes=None)
# X_list = [process_file(x) for x in get_file_paths(path, HARD_MAX)]
X_list = pool.map(process_file, get_file_paths(path, HARD_MAX))
X_list = [x for x in X_list if x is not None]
        
print(f'Passes {len(X_list):6}/{HARD_MAX:6} hard max')
X = pd.DataFrame(pd.concat(X_list), columns=columns)
X = X.set_index(['name', 'time'])

X.to_pickle(os.path.join(path, 'X_saved.gzip'))

Processing ../data/Party Rock Anthem/blocks/ExpertPlus.pkl
Processing ../data/1My Truth/blocks/Hard.pkl
Processing ../data/LAST GAME (TV-Size)/blocks/Hard.pkl
Processing ../data/time to say goodbye/blocks/ExpertPlus.pkl
Processing ../data/LAST GAME (TV-Size)/blocks/Expert.pkl
Processing ../data/Party Rock Anthem/blocks/Expert.pkl
Processing ../data/Seven Nation Army/blocks/Hard.pkl
Processing ../data/BTH 6 - Sweet Lies/blocks/ExpertPlus.pkl
Processing ../data/BTH 6 - Hot Right Now/blocks/Expert.pkl
Processing ../data/ODESZA-LineOfSight/blocks/Hard.pkl
#    0 ../data/1My Truth/blocks/Hard.pkl
#    1 ../data/BTH 6 - Sweet Lies/blocks/ExpertPlus.pkl
#    2 ../data/Seven Nation Army/blocks/Hard.pkl
#    3 ../data/LAST GAME (TV-Size)/blocks/Hard.pkl
#    4 ../data/LAST GAME (TV-Size)/blocks/Expert.pkl
#    5 ../data/Party Rock Anthem/blocks/ExpertPlus.pkl
#    6 ../data/Party Rock Anthem/blocks/Expert.pkl
#    7 ../data/time to say goodbye/blocks/ExpertPlus.pkl
#    8 ../data/BTH 6 - Hot Ri

In [176]:
X

times  \
name                                        time                                                     
../data/1My Truth/blocks/Hard.pkl           2.527397      [2.5273972602739727, 0.8219178082191778]   
                                            3.349315      [0.8219178082191778, 0.8219178082191778]   
                                            4.171233      [0.8219178082191778, 0.2054794520547949]   
                                            4.376712      [0.2054794520547949, 0.2054794520547949]   
                                            4.582192      [0.2054794520547949, 0.2054794520547949]   
                                            4.787671      [0.2054794520547949, 0.2054794520547949]   
                                            4.993151      [0.2054794520547949, 0.8219178082191778]   
                                            5.815068      [0.8219178082191778, 0.8219178082191769]   
                                            6.636986      [0.8219178082191769, 0.2054794520547949]   
                                            6.842466      [0.2054794520547949, 0.2054794520547949]   
                                            7.047945      [0.2054794520547949, 0.2054794520547949]   
                                            7.253425      [0.2054794520547949, 0.2054794520547949]   
                                            7.458904      [0.2054794520547949, 1.2328767123287676]   
                                            8.691781      [1.2328767123287676, 0.4109589041095898]   
                                            9.102740      [0.4109589041095898, 0.6164383561643838]   
                                            9.719178       [0.6164383561643838, 0.205479452054794]   
                                            9.924658       [0.205479452054794, 1.7054794520547958]   
                                            11.630137     [1.7054794520547958, 0.4232876712328757]   
                                            12.053425    [0.4232876712328757, 0.38630136986301444]   
                                            12.439726    [0.38630136986301444, 0.7849315068493148]   
                                            13.224658     [0.7849315068493148, 0.8095890410958901]   
                                            14.034247      [0.8095890410958901, 0.205479452054794]   
                                            14.239726       [0.205479452054794, 0.205479452054794]   
                                            14.445205       [0.205479452054794, 0.205479452054794]   
                                            14.650685       [0.205479452054794, 0.205479452054794]   
                                            14.856164      [0.205479452054794, 0.8712328767123303]   
                                            15.727397     [0.8712328767123303, 0.7849315068493148]   
                                            16.512329    [0.7849315068493148, 0.20547945205479579]   
                                            16.717808   [0.20547945205479579, 0.23013698630137114]   
                                            16.947945    [0.23013698630137114, 0.1726027397260239]   
...                                                                                            ...   
../data/Army Of The Night/blocks/Expert.pkl 169.818947    [0.3157894736842195, 0.3157894736842195]   
                                            170.134737    [0.3157894736842195, 0.3157894736842195]   
                                            170.450526    [0.3157894736842195, 0.3157894736842195]   
                                            170.766316   [0.3157894736842195, 0.15789473684210975]   
                                            170.924211   [0.15789473684210975, 0.3157894736842195]   
                                            171.240000    [0.3157894736842195, 0.3157894736842195]   
                                            171.555789    [0.3157894736842195, 0.3157894736842195]   
             

In [177]:
def pp(row):
    print('*' * 69)
    print(row)
    
def round_up(num:float, prec: int) -> int:
    return int(math.ceil((10 ** prec) * num) / (10 ** prec))
    
def get_len_category(song):
    return round_up(len(song), -2)

def get_mask(X):
    mask = X.groupby('name').apply(get_len_category)
    return mask.to_dict()

In [178]:
grouped = X.groupby(get_mask(X), level=0)

for name, group in grouped:
    print(f'{name}: {len(group.groupby("name").groups)}')

100: 1
200: 1
300: 1
400: 2
500: 4
600: 2
700: 2
800: 3
900: 1
1000: 3
1300: 1


In [179]:
def create_batch(group, ceil_len):
    print(f'Creating batch of ceil_len {ceil_len:6} with {len(group)} rows')
    
    batch = []
    for name, song in group.groupby('name'):
#         print(f'{l} {name}')
        empty_row = song.tail(1).squeeze().apply(np.zeros_like)
        df_to_add = pd.DataFrame([empty_row] * (ceil_len - len(song)))
        batch.append(pd.concat([song, df_to_add]))

    return pd.concat(batch)

In [19]:
def list2numpy(batch, col_name):
    return np.array(batch.groupby('name')[col_name].apply(list).to_list())
#     return np.array(batch[col_name].to_list())

def train_generator(df):
    grouped = X.groupby(get_mask(df), level=0)
    batches = [create_batch(group, ceil_len) for ceil_len, group in grouped]
    batches = [batch for batch in batches if len(batch.groupby('name').groups) > 8]
    
    while True:
        for batch in batches:
            yield [list2numpy(batch, 'shifted'), list2numpy(batch, 'times')], list2numpy(batch, 'output')

In [20]:
list2numpy(X, 'shifted')[:10]

array([list([array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.]), array([0., 0., 0., 0., 0., 0.,

### Concatering model

In [21]:
from keras.layers import Dense, LSTM, Flatten, Input, Activation, TimeDistributed, concatenate
from keras.models import Sequential
from keras.models import Model

In [80]:
def get_model():
    in1 = Input(shape=(None, 216)) # last blocks
    in2 = Input(shape=(None, 2))   # time difference of previous and next beat
    
    x1 = TimeDistributed(Dense(50, activation='elu'))(in1)
    x2 = TimeDistributed(Dense(3, activation='elu'))(in2)
    
    out = concatenate([x1, x2], axis=-1)
    out = LSTM(50, return_sequences=True)(out)
    out = TimeDistributed(Dense(216, activation='sigmoid'))(out)

    model = Model(inputs=[in1, in2], outputs=out)
    
    model.compile(optimizer='adam',
                  loss='binary_crossentropy',
#                   loss='categorical_crossentropy',
                  metrics=['accuracy', 'binary_crossentropy'])
    
    return model

In [81]:
model = get_model()
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_21 (InputLayer)           (None, None, 216)    0                                            
__________________________________________________________________________________________________
input_22 (InputLayer)           (None, None, 2)      0                                            
__________________________________________________________________________________________________
time_distributed_31 (TimeDistri (None, None, 50)     10850       input_21[0][0]                   
__________________________________________________________________________________________________
time_distributed_32 (TimeDistri (None, None, 3)      9           input_22[0][0]                   
__________________________________________________________________________________________________
concatenat

In [82]:
model = get_model()
generator = train_generator(X)

In [83]:
counter = 0
hard_counter = 0
hard_max = 120

for x, y in generator:
    if counter > 14 or hard_counter > hard_max:
        break
    res = model.fit(x, y, batch_size=32, validation_split=0.1)
    
    if res.history['val_acc'][-1] > 0.99:
        counter += 1
    hard_counter += 1
    print('Result: ', res.history['val_acc'])

# model.predict()

Creating batch of ceil_len    100 with 277 rows
Creating batch of ceil_len    200 with 4314 rows
Creating batch of ceil_len    300 with 26962 rows
Creating batch of ceil_len    400 with 85821 rows
Creating batch of ceil_len    500 with 141112 rows
Creating batch of ceil_len    600 with 144392 rows
Creating batch of ceil_len    700 with 117966 rows
Creating batch of ceil_len    800 with 98190 rows
Creating batch of ceil_len    900 with 62471 rows
Creating batch of ceil_len   1000 with 45787 rows
Creating batch of ceil_len   1100 with 32107 rows
Creating batch of ceil_len   1200 with 18205 rows
Creating batch of ceil_len   1300 with 5017 rows
Creating batch of ceil_len   1400 with 8151 rows
Creating batch of ceil_len   1500 with 7166 rows
Creating batch of ceil_len   1600 with 4540 rows
Creating batch of ceil_len   1700 with 1698 rows
Creating batch of ceil_len   1800 with 1729 rows
Creating batch of ceil_len   2300 with 2219 rows
Creating batch of ceil_len   2600 with 2592 rows
Train on

In [96]:
import copy

x, y = generator.__next__()
prediction = model.predict(x)
print(prediction.shape)
print(y.shape)
# model2 = copy.deepcopy(model)

(25, 200, 216)
(25, 200, 216)


In [100]:
# prediction[1].max(1)
prediction[1][1]

array([0.28019655, 0.2997747 , 0.3028502 , 0.25510705, 0.2715386 ,
       0.27823758, 0.272296  , 0.2622844 , 0.24979186, 0.21455336,
       0.27836883, 0.27256718, 0.27257293, 0.26598722, 0.28068793,
       0.26494667, 0.26894742, 0.28877664, 0.30038667, 0.34958553,
       0.27095336, 0.25719237, 0.2999833 , 0.28345641, 0.2736444 ,
       0.277958  , 0.2954566 , 0.29503274, 0.2719962 , 0.2640256 ,
       0.22962299, 0.242306  , 0.22715938, 0.26251075, 0.27928513,
       0.23054096, 0.26184618, 0.287098  , 0.2509739 , 0.2739464 ,
       0.25623763, 0.24143174, 0.2467432 , 0.25459784, 0.27298605,
       0.30263016, 0.35252562, 0.278872  , 0.2791006 , 0.26507112,
       0.23742709, 0.26097557, 0.24688217, 0.25137916, 0.26002717,
       0.25458658, 0.24450102, 0.2969437 , 0.30226135, 0.27853614,
       0.22402114, 0.2912507 , 0.25751936, 0.28541303, 0.30540213,
       0.27835605, 0.24838841, 0.26523006, 0.29395837, 0.29218614,
       0.28330415, 0.28877646, 0.2795683 , 0.23682922, 0.29763

In [66]:
# def train_generator():
#     while True:
#         for x1, x2, y in zip(X['blocks'][:300], X['times'][:300], Y[:300]):
#             yield [np.array([x1, ]), np.array([x2, ])], np.array([y, ])
            
def eval_generator():
    while True:
        for x1, x2, y in zip(X['blocks'][300:], X['times'][300:], Y[300:]):
            yield [np.array([x1, ]), np.array([x2, ])], np.array([y, ])
            
model = get_model()
model.batch_size = 8            

model.fit_generator(train_generator(), steps_per_epoch=300, epochs=1, verbose=1, 
                    use_multiprocessing=False)
model.evaluate_generator(eval_generator(), steps=19, )

TypeError: train_generator() missing 1 required positional argument: 'df'

# Multi input test

In [ ]:
from keras.layers import Dense ,LSTM,concatenate,Input,Flatten
import tensorflow as tf
import matplotlib
import numpy as np
import pandas as pd
from keras.models import Model
from keras.callbacks import EarlyStopping
#
def model(i,p,data_a,data_b,labels):
#     #x=tf.placeholder(tf.float32,shape=(i,1,None))
#     x=Input(shape=(None, 2))
#     #x = Flatten()(x)
#     y=Input(shape=(None, 4))
#     #y = Flatten()(y)
#     #y=tf.placeholder(tf.float32,shape=(i,1,None))
#     #LSTM layers
#     admi=LSTM(40,return_sequences=True)(x)
#     pla=LSTM(40,return_sequences=True)(y)
#     out=concatenate([admi,pla],axis=-1)
#     print(pla)
#     #out=Flatten(input_shape=(None,1))(out)
#     print(out)
#     #out=np.reshape(out,(1,9))
#     output=TimeDistributed(Dense(1, activation='sigmoid'))(out)
#     model = Model(inputs=[x, y], outputs=output)
#     model.compile(optimizer='rmsprop',
#               loss='binary_crossentropy',
#               metrics=['accuracy'])
    n=model.fit([data_a, data_b],labels,batch_size=1, epochs=10)
    return n

# data_a=np.array([300,455,350,560,700,800,200,250,300])
# labes=np.array([455,350,560,700,800,200,250,300,350])
# data_b=np.array([200,255,350,470,600,300,344,322,300])
# data_a=np.reshape(data_a,(9,1,1))
# data_b=np.reshape(data_b,(9,1,1))


data_a = np.random.rand(9, 2, 2)
data_b = np.random.rand(9, 2, 4)
labels = np.random.rand(9, 2, 1)

#s=labes.shape()
#labes=np.reshape(labes,(1,9,1))
print(data_a.shape)
print(data_b.shape)
print(labels.shape)

#labes=labes(9,4)
#data_b=tf.placeholder(tf.float32,shape=(6,1))

#labes=tf.placeholder(tf.float32,shape=(6,1))

re = model(1,4,data_a,data_b,labels)
print(re)

In [ ]:
df = pd.DataFrame({'Col1': [10, 20, 15, 30, 45],
...                    'Col2': [13, 23, 18, 33, 48],
...                    'Col3': [17, 27, 22, 37, 52]})
df

In [ ]:
df['Col11'] = pd.Series([np.zeros((206, 1))] * 5)
df['Col11'] = df['Col11'].shift(-1, fill_value=[np.zeros((206, 1))])
df